In [1]:
import glob,os,h5py
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from pycbc.inference import io, models
from pycbc.workflow import WorkflowConfigParser
from pycbc import conversions
# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

# Compute the SNR

In [16]:
from pycbc import cosmology
path = ['/work/yifan.wang/4ogc/release_prod/shichao_extract/',
        '/work/yifan.wang/4ogc/release_prod/yifan/',
        '/work/yifan.wang/4ogc/release_prod/shilpa/',
        '/work/yifan.wang/4ogc/release_prod/sumit/']
#path = ['/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/']
#read in the posfiles
posfiles = []
for p in path:
    f = glob.glob(p+'/*.hdf')
    posfiles.extend(f)
    
def custom_sort(name):
    return name.split('GW')[1][:13]

#remove BNS events:
#posfiles.remove('/work/yifan.wang/4ogc/release_prod/sumit/GW170817_124104-PYCBC-POSTERIOR-XPHM-LOWSPIN-PRIOR-FIXED-RADEC.hdf')
#posfiles.remove('/work/yifan.wang/4ogc/release_prod/yifan/inference_extract_GW190425_081805.hdf')
#posfiles.remove('/work/yifan.wang/4ogc/release_prod/shichao_extract/GW200105_162426-PYCBC-POSTERIOR-IMRPhenomNSBH_LOWSPIN_RELBIN.hdf',)
#posfiles.remove('/work/yifan.wang/4ogc/release_prod/sumit/GW200115_042309-PYCBC-POSTERIOR-XPHM-LOWSPIN-PRIORS.hdf')
posfiles.sort(key=custom_sort)
gwnames = []
for i,path in enumerate(posfiles):
    gwnames.append('GW'+path.split('GW')[1][:13])

#read in the config files
config_files =glob.glob('/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/*.ini')

#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200115_042309_clean_highspin.ini')
#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw170817_124104_lowspin_prior_fixed_radec.ini')
#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/yifan_config/inference-GW190425_081805.ini')
#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/shichao_config/inference-GW200115_042309_NSBH_lowspin_relbin_deglitched.ini')
#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/shichao_config/inference-GW200105_162426_NSBH_lowspin_relbin_deglitched.ini')
#config_files.remove('/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200115_042309_clean_lowspin.ini')

def config_sort(name):
    return os.path.basename(name)[12:25]
config_files.sort(key=config_sort)

In [17]:
len(posfiles),len(config_files)

(94, 94)

In [21]:
snrs = {}
q = {}
for ii,posfile in enumerate(posfiles):
    print(gwnames[ii])
    fp = io.loadfile(posfile, 'r')
    #GW170304 has a problem for reading in config file, not sure why, 
    #at the moment manually load the config file for it
    cp = WorkflowConfigParser([config_files[ii]])
    data = fp.read_data()
    psds = fp.read_psds()

    samples = fp.read_samples(fp['samples'].keys())
    idx = samples['loglikelihood'].argmax()
    maxl_params = {p: samples[p][idx] for p in samples.fieldnames}
    maxl_params['tc'] = fp.attrs['trigger_time'] + maxl_params['delta_tc']
    #add q
    q[gwnames[ii]] = [np.quantile(samples['q'],0.05),np.quantile(samples['q'],0.5),np.quantile(samples['q'],0.95)]
    fp.close()
    #maxL parameters include maxl_polarization
    #TODO: include maxl_polarization

    gate_start = str(maxl_params['tc'] - 8)
    gate_end = str(maxl_params['tc'])

    cp.set('model', 'name', 'gated_gaussian_margpol')
    cp.set('static_params', 't_gate_start', gate_start)
    cp.set('static_params', 't_gate_end', gate_end)
    
    # The gated_gaussian_noise model failed with the next line for not providing "location"
    try:
        model = models.read_from_config(cp, data=data, psds=psds)
    except (TypeError,ValueError) as e:
        #GW190725 has been rerun, but there is problem because all ifo should have same deltaf
        continue
    # force the sampling transforms to None so you can update the
    # model with the variable params below
    model.sampling_transforms = None

    maxl_params['comoving_volume'] = cosmology.cosmological_quantity_from_redshift(
                    maxl_params['redshift'], 'comoving_volume')
    maxl_params['mass1'] = maxl_params['srcmass1'] * (1+maxl_params['redshift'])
    maxl_params['mass2'] = maxl_params['srcmass2'] * (1+maxl_params['redshift'])
    maxl_var_params = {p: maxl_params[p] for p in model.variable_params}

    model.update(**maxl_var_params)
    loglr = model.loglr
    snr = conversions.snr_from_loglr(loglr)
    print(snr)
    snrs[gwnames[ii]] = snr

GW150914_095045


12.467077295846217
GW151012_095443
3.668583331357774
GW151226_033853


0.671974343202256
GW170104_101158
5.627408065722992
GW170121_212536


5.033580776038317
GW170202_135657


0.9749894750193149
GW170304_163753


...

3.5667055335037725
GW200306_093714


1.826787222153779
GW200311_115853


6.495875156493358
GW200316_215756


1.0962746662898457
GW200318_191337


3.837060737515047


In [22]:
snrs

{'GW150914_095045': 12.467077295846217,
 'GW151012_095443': 3.668583331357774,
 'GW151226_033853': 0.671974343202256,
 'GW170104_101158': 5.627408065722992,
 'GW170121_212536': 5.033580776038317,
 'GW170202_135657': 0.9749894750193149,
 'GW170304_163753': 3.7130136954993507,
 'GW170403_230611': 5.038966901200345,
 'GW170608_020116': 0.41691279828138955,
 'GW170727_010430': 4.603189447926829,
 'GW170729_185629': 4.945820644415321,
 'GW170809_082821': 4.0463421824170895,
 'GW170814_103043': 5.815658660786181,
 'GW170818_022509': 5.220904800497316,
 'GW170823_131358': 4.252757372243574,
 'GW190404_142514': 2.6010831953120594,
 'GW190408_181802': 4.782827286557121,
 'GW190412_053044': 5.623978204347797,
 'GW190413_052954': 5.084998739019845,
 'GW190413_134308': 5.494623386082732,
 'GW190421_213856': 4.397904624554849,
 'GW190424_180648': 4.532966786294299,
 'GW190427_180650': 1.4192767238640525,
 'GW190503_185404': 5.182898009259062,
 'GW190512_180714': 4.580864820148413,
 'GW190513_205428

In [23]:
q

{'GW150914_095045': [1.0188566861548156,
  1.1714739527857558,
  1.5277957450652155],
 'GW151012_095443': [1.1154176590786737, 2.0035954786447894, 4.1281886602535],
 'GW151226_033853': [1.0954923510001655,
  1.9219288656284133,
  4.465366973934092],
 'GW170104_101158': [1.0812213036077467,
  1.5326398001454165,
  2.2688644475765205],
 'GW170121_212536': [1.0351873634335187,
  1.3282665325808072,
  2.0463338604824024],
 'GW170202_135657': [1.106149136297556, 1.971768227430721, 3.9665334568825363],
 'GW170304_163753': [1.0496869253584258,
  1.4252393815177395,
  2.5150539626307853],
 'GW170403_230611': [1.0393449729641862,
  1.3410787920328446,
  2.3356880303977943],
 'GW170608_020116': [1.0431218782177523,
  1.4238853232866868,
  2.812236983440622],
 'GW170727_010430': [1.0394522204280432,
  1.349092131831648,
  2.1671232972492978],
 'GW170729_185629': [1.0917233717703219,
  1.6868189881598148,
  2.749752694999933],
 'GW170809_082821': [1.0450518318421085,
  1.3946383652929475,
  2.1699

# I/O json dict

In [10]:
import json

snrs = {"GW150914_095045": 12.467077324310226, "GW151012_095443": 3.6685833324366977, "GW151226_033853": 0.6719741791404517, "GW170104_101158": 5.627407996581194, "GW170121_212536": 5.033580791765177, "GW170202_135657": 0.9749894929967209, "GW170304_163753": 3.7130136952406856, "GW170403_230611": 5.038966918823613, "GW170608_020116": 0.4169132696244449, "GW170727_010430": 4.603185182995048, "GW170729_185629": 4.945820562867502, "GW170809_082821": 4.046342181589938, "GW170814_103043": 5.815658659950448, "GW170818_022509": 5.220904797285022, "GW170823_131358": 4.2527573773385745, "GW190404_142514": 2.601083195228141, "GW190408_181802": 4.782827077267279, "GW190412_053044": 5.623978319376681, "GW190413_052954": 5.0849987392602305, "GW190413_134308": 5.494623378995636, "GW190421_213856": 4.397904622711831, "GW190424_180648": 4.53296678516911, "GW190427_180650": 1.3689186399873594, "GW190503_185404": 5.1828980106741325, "GW190512_180714": 4.580864835351976, "GW190513_205428": 5.6358214849160895, "GW190514_065416": 4.382739226586209, "GW190517_055101": 4.215721686576801, "GW190519_153544": 8.588455019298905, "GW190521_030229": 12.739953110529152, "GW190521_074359": 9.486222248503463, "GW190527_092055": 1.4675195046549383, "GW190602_175927": 7.343629009373758, "GW190620_030421": 7.101782025788102, "GW190630_185205": 3.4334508141373807, "GW190701_203306": 6.052363605443309, "GW190706_222641": 7.495015245794337, "GW190707_093326": 1.7263344282100506, "GW190708_232457": 3.4490401064057723, "GW190719_215514": 1.2063896275888746, "GW190720_000836": 1.7648529385709943, "GW190725_174728": 1.4282378468969061, "GW190727_060333": 5.551577756078929, "GW190728_064510": 0.9750126021744511, "GW190731_140936": 4.033655705622703, "GW190803_022701": 4.37902581525848, "GW190805_105432": 1.9308379551845738, "GW190814_211039": 3.234199950818591, "GW190828_063405": 6.374632326947989, "GW190828_065509": 0.0, "GW190910_112807": 6.003467660890636, "GW190915_235702": 5.219321819917709, "GW190916_200658": 4.118518048727367, "GW190924_021846": 0.6895825751489296, "GW190925_232845": 2.9511678847799394, "GW190926_050336": 2.975783886724292, "GW190929_012149": 3.262234619661963, "GW190930_133541": 1.099075427328961, "GW191105_143521": 1.4421325445811883, "GW191109_010717": 11.2742573312186, "GW191126_115259": 0.0, "GW191127_050227": 4.2184268801184075, "GW191129_134029": 0.0, "GW191204_110529": 3.0242595948313435, "GW191204_171526": 3.5542665975142413, "GW191215_223052": 4.734884600216645, "GW191216_213338": 0.0, "GW191222_033537": 4.959889541101508, "GW191224_043228": 2.4723197567420865, "GW191230_180458": 4.943941655386827, "GW200106_134123": 4.882961251472598, "GW200112_155838": 7.87326753698052, "GW200128_022011": 5.072161884998413, "GW200129_065458": 13.064978582638986, "GW200129_114245": 3.8268266661312778, "GW200202_154313": 1.6234431627927914, "GW200208_130117": 4.583727298805941, "GW200209_085452": 4.772958002094568, "GW200210_005122": 0.0, "GW200214_223307": 2.689409868572342, "GW200216_220804": 4.703717687678236, "GW200219_094415": 3.0179713773030907, "GW200224_222234": 10.432278621813069, "GW200225_060421": 3.982162341390009, "GW200302_015811": 4.664316385563981, "GW200305_084739": 3.566705539937825, "GW200306_093714": 1.8267872912495713, "GW200311_115853": 6.495875164195089, "GW200316_215756": 1.0962746902891802, "GW200318_191337": 3.8370607312309337}

with open('snrs.json', 'w') as f:
     f.write(json.dumps(snrs))

In [13]:
f = open('snrs.json')
 
# returns JSON object as
# a dictionary
data = json.load(f)

In [25]:
snrs_ge4 = {}
for event in snrs:
    if snrs[event] >= 4:
        snrs_ge4[event] = snrs[event]

In [45]:
#output latex
i = 1
for event in snrs_ge4:
    color=''
    if i%2==0:
        color=r'\rowcolor{Gray}'
    print(color+str(i)+' & '+str(event.split('_')[0]+'\_'+event.split('_')[1])+' & {:.4f} \\\\'.format(snrs_ge4[event]))
    i+=1

1 & GW150914\_095045 & 12.4671 \\
\rowcolor{Gray}2 & GW170104\_101158 & 5.6274 \\
3 & GW170121\_212536 & 5.0336 \\
\rowcolor{Gray}4 & GW170403\_230611 & 5.0390 \\
5 & GW170727\_010430 & 4.6032 \\
\rowcolor{Gray}6 & GW170729\_185629 & 4.9458 \\
7 & GW170809\_082821 & 4.0463 \\
\rowcolor{Gray}8 & GW170814\_103043 & 5.8157 \\
9 & GW170818\_022509 & 5.2209 \\
\rowcolor{Gray}10 & GW170823\_131358 & 4.2528 \\
11 & GW190408\_181802 & 4.7828 \\
\rowcolor{Gray}12 & GW190412\_053044 & 5.6240 \\
13 & GW190413\_052954 & 5.0850 \\
\rowcolor{Gray}14 & GW190413\_134308 & 5.4946 \\
15 & GW190421\_213856 & 4.3979 \\
\rowcolor{Gray}16 & GW190424\_180648 & 4.5330 \\
17 & GW190503\_185404 & 5.1829 \\
\rowcolor{Gray}18 & GW190512\_180714 & 4.5809 \\
19 & GW190513\_205428 & 5.6358 \\
\rowcolor{Gray}20 & GW190514\_065416 & 4.3827 \\
21 & GW190517\_055101 & 4.2157 \\
\rowcolor{Gray}22 & GW190519\_153544 & 8.5885 \\
23 & GW190521\_030229 & 12.7400 \\
\rowcolor{Gray}24 & GW190521\_074359 & 9.4862 \\
25 & GW1906